In [1]:
import numpy as np
import cv2
import pandas as pd
from imageio import imread
import matplotlib.pyplot as plt
import png
from scipy import ndimage
import sys

In [2]:
def image_as_png(image, png_filename, bitdepth=16):

    
    with open(png_filename, 'wb') as f:
        writer = png.Writer(
            height=image.shape[0],
            width=image.shape[1],
            bitdepth=bitdepth,
            greyscale=True
        )
        writer.write(f, image.tolist())
        
        print("done!")

In [3]:
def crop_val(v, minv, maxv):
    v = v if v >= minv else minv
    v = v if v <= maxv else maxv
    return v


In [4]:
def add_img_margins(img, margin_size):
    '''Add all zero margins to an image
    '''
    enlarged_img = np.zeros((img.shape[0]+margin_size*2, 
                             img.shape[1]+margin_size*2))
    enlarged_img[margin_size:margin_size+img.shape[0], 
                 margin_size:margin_size+img.shape[1]] = img
    return enlarged_img

In [5]:
def segment_breast( img,mask, low_int_threshold=.05, crop=True):
        '''Perform breast segmentation
        Args:
            low_int_threshold([float or int]): Low intensity threshold to 
                    filter out background. It can be a fraction of the max 
                    intensity value or an integer intensity value.
            crop ([bool]): Whether or not to crop the image.
        Returns:
            An image of the segmented breast.
        NOTES: the low_int_threshold is applied to an image of dtype 'uint8',
            which has a max value of 255.
        '''
        # Create img for thresholding and contours.
        img_8u = (img.astype('float32')/img.max()*255).astype('uint8')
        if low_int_threshold < 1.:
            low_th = int(img_8u.max()*low_int_threshold)
        else:
            low_th = int(low_int_threshold)
        _, img_bin = cv2.threshold(
            img_8u, low_th, maxval=255, type=cv2.THRESH_BINARY)
        ver = (cv2.__version__).split('.')
        if int(ver[0]) < 3:
            contours,_ = cv2.findContours(
                img_bin.copy(), cv2.RETR_TREE, cv2.CHAIN_APPROX_SIMPLE)
        else:
            contours,_ = cv2.findContours(
                img_bin.copy(), cv2.RETR_TREE, cv2.CHAIN_APPROX_SIMPLE)
        cont_areas = [ cv2.contourArea(cont) for cont in contours ]
        idx = np.argmax(cont_areas)  # find the largest contour, i.e. breast.
        breast_mask = cv2.drawContours(
            np.zeros_like(img_bin), contours, idx, 255, -1)  # fill the contour.
        # segment the breast.
        img_breast_only = cv2.bitwise_and(img, img, mask=breast_mask)
        img_mask = cv2.bitwise_and(mask, mask, mask=breast_mask)
        x,y,w,h = cv2.boundingRect(contours[idx])
        if crop:
            img_breast_only = img_breast_only[y:y+h, x:x+w]
            mask = img_mask[y:y+h, x:x+w]
            
        return img_breast_only, mask

In [6]:
def overlap_patch_roi(patch_center, patch_size, roi_mask, 
                      add_val=1000, cutoff=.9):
    x1,y1 = (patch_center[0] - int(patch_size/2), 
             patch_center[1] - int(patch_size/2))
    x2,y2 = (patch_center[0] + int(patch_size/2), 
             patch_center[1] + int(patch_size/2))
    x1 = crop_val(x1, 0, roi_mask.shape[1])
    y1 = crop_val(y1, 0, roi_mask.shape[0])
    x2 = crop_val(x2, 0, roi_mask.shape[1])
    y2 = crop_val(y2, 0, roi_mask.shape[0])
    
    roi_area = (roi_mask>0).sum()
    roi_patch_added = roi_mask.copy()
    roi_patch_added = roi_patch_added.astype('uint16')
    roi_patch_added[y1:y2, x1:x2] += add_val
    patch_area = (roi_patch_added>=add_val).sum()
    inter_area = (roi_patch_added>add_val).sum().astype('float32')
   
    return (inter_area/roi_area > cutoff or inter_area/patch_area > cutoff)

In [7]:
def sample_patches(img_,index,label, roi_mask_,patch_size=256,
                   pos_cutoff=.9, neg_cutoff=.35,
                   nb_bkg=11, nb_abn=10, start_sample_nb=0,
                   verbose=True):

    index = int(index)
    print(index)
    img,roi_mask = segment_breast(img_,roi_mask_)
    if roi_mask.sum()== 0:
        roi_mask = roi_mask_
        img= img_
    
    if img.shape == roi_mask.shape:
        
        print("img and mask shape match")
        
        img = add_img_margins(img, int(patch_size/2))
        roi_mask = add_img_margins(roi_mask, int(patch_size/2))
        roi_mask = roi_mask.astype("uint8")
        # Get ROI bounding box.
        _, thresh = cv2.threshold(roi_mask, 254, 255, cv2.THRESH_BINARY)


        contours,_ = cv2.findContours(
                thresh, cv2.RETR_TREE, cv2.CHAIN_APPROX_SIMPLE)
        cont_areas = [ cv2.contourArea(cont) for cont in contours ]
        
        idx = np.argmax(cont_areas)  # find the largest contour.
        rx,ry,rw,rh = cv2.boundingRect(contours[idx])

        cy,cx = ndimage.measurements.center_of_mass(thresh)
        cy = int(round(cy,0))
        cx = int(round(cx,0))

        print("ROI centroid=", (cx,cy)); sys.stdout.flush()
        patch_center = (cx,cy)
        x1,y1 = (patch_center[0] - int(patch_size/2), 
                 patch_center[1] - int(patch_size/2))
        x2,y2 = (patch_center[0] + int(patch_size/2), 
                 patch_center[1] + int(patch_size/2))
        x1 = crop_val(x1, 0, roi_mask.shape[1])
        y1 = crop_val(y1, 0, roi_mask.shape[0])
        x2 = crop_val(x2, 0, roi_mask.shape[1])
        y2 = crop_val(y2, 0, roi_mask.shape[0])

        s_patch = img[y1:y2, x1:x2]
        s_patch= s_patch.astype('uint16')
        
        pathi = "/home/sposso22/Desktop/Breast_cancer/patches_256/s/" +"roi_"+ str(index) + ".png"
        image_as_png(s_patch,pathi)
        s_path.append(pathi)
        s_class.append(label)


        rng = np.random.RandomState(321)
        # Sample abnormality first.
        sampled_abn = 0
        nb_try = 0
        while sampled_abn < nb_abn:
            x = rng.randint(rx, rx + rw)
            y = rng.randint(ry, ry + rh)
            nb_try += 1
            if nb_try > 1000:
                print("Nb of trials reached maximum, decrease overlap cutoff by 0.05")
                sys.stdout.flush()
                pos_cutoff -= .05
                nb_try = 0
                if pos_cutoff <= .0:
                    raise Exception("overlap cutoff becomes non-positive, "
                                    "check roi mask input.")
            # import pdb; pdb.set_trace()

            if overlap_patch_roi((x,y), patch_size, roi_mask, cutoff=pos_cutoff):
                patch = img[y - int(patch_size/2):y + int(patch_size/2), 
                            x - int(patch_size/2):x + int(patch_size/2)]

                path_s10 = "/home/sposso22/Desktop/Breast_cancer/patches_256/s10/" +"roi_"+ str(index)+"_"+str(sampled_abn)+".png"
                patch= patch.astype('uint16')
                
                image_as_png(patch,path_s10)
                s10_path.append(path_s10)
                s10_class.append(label)
                sampled_abn += 1
                nb_try = 0
                if verbose:
                    print("sampled an abn patch at (x,y) center=", (x,y))
                    sys.stdout.flush()
        # Sample background.
        sampled_bkg = start_sample_nb
        count = 0
        while sampled_bkg < start_sample_nb + nb_bkg:
            x = rng.randint(int(patch_size/2), img.shape[1] - int(patch_size/2))
            y = rng.randint(int(patch_size/2), img.shape[0] - int(patch_size/2))
            if not overlap_patch_roi((x,y), patch_size, roi_mask, cutoff=neg_cutoff):
                bkg = img[y - int(patch_size/2):y + int(patch_size/2), 
                            x - int(patch_size/2):x + int(patch_size/2)]


                sampled_bkg += 1

                if sampled_bkg ==1:

                    bkg_s_path = "/home/sposso22/Desktop/Breast_cancer/patches_256/s/" +"bkg_"+ str(index) +".png"
                    bkg= bkg.astype('uint16')
                    image_as_png(bkg,bkg_s_path)
                    s_path.append(bkg_s_path)
                    s_class.append(0)

                else:

                    bkg_s_path = "/home/sposso22/Desktop/Breast_cancer/patches_256/s10/" +"bkg_"+ str(index)+"_"+str(sampled_bkg)+".png"
                    bkg= bkg.astype('uint16')
                    image_as_png(bkg,bkg_s_path)
                    s10_path.append(bkg_s_path)
                    s10_class.append(0)


                if verbose:
                    print("sampled a bkg patch at (x,y) center=", (x,y))
                    sys.stdout.flush()
                    
    else:
        print("mask and img have different shape")
   

In [8]:
data = pd.read_csv("/home/sposso22/Desktop/Breast_cancer/df_png.csv")

In [9]:

s = pd.DataFrame()
s10 = pd.DataFrame()
s_path =[]
s_class =[]
count_ = 0
s10_class =[]
s10_path =[]
bad = 0


In [10]:
for index in range(len(data)):
    print(data['mask_path'][index])
    mam = imread(data['img_path'][index])
    mask = imread(data['mask_path'][index])
    label = data['label'][index]
    
    sample_patches(mam,index,label,mask)
    

/home/sposso22/Desktop/Breast_cancer/roi/mask_0.png
0
img and mask shape match
ROI centroid= (260, 781)
done!
done!
sampled an abn patch at (x,y) center= (266, 733)
done!
sampled an abn patch at (x,y) center= (214, 785)
done!
sampled an abn patch at (x,y) center= (258, 715)
done!
sampled an abn patch at (x,y) center= (300, 716)
done!
sampled an abn patch at (x,y) center= (217, 813)
done!
sampled an abn patch at (x,y) center= (233, 834)
done!
sampled an abn patch at (x,y) center= (281, 712)
done!
sampled an abn patch at (x,y) center= (230, 837)
done!
sampled an abn patch at (x,y) center= (254, 832)
done!
sampled an abn patch at (x,y) center= (289, 711)
done!
sampled a bkg patch at (x,y) center= (159, 666)
done!
sampled a bkg patch at (x,y) center= (631, 826)
done!
sampled a bkg patch at (x,y) center= (695, 1140)
done!
sampled a bkg patch at (x,y) center= (859, 702)
done!
sampled a bkg patch at (x,y) center= (474, 146)
done!
sampled a bkg patch at (x,y) center= (825, 539)
done!
sampled a

done!
sampled an abn patch at (x,y) center= (372, 1032)
done!
sampled a bkg patch at (x,y) center= (653, 427)
done!
sampled a bkg patch at (x,y) center= (566, 190)
done!
sampled a bkg patch at (x,y) center= (543, 1015)
done!
sampled a bkg patch at (x,y) center= (183, 1186)
done!
sampled a bkg patch at (x,y) center= (562, 1164)
done!
sampled a bkg patch at (x,y) center= (609, 142)
done!
sampled a bkg patch at (x,y) center= (650, 641)
done!
sampled a bkg patch at (x,y) center= (545, 878)
done!
sampled a bkg patch at (x,y) center= (203, 495)
done!
sampled a bkg patch at (x,y) center= (144, 851)
done!
sampled a bkg patch at (x,y) center= (295, 414)
/home/sposso22/Desktop/Breast_cancer/roi/mask_7.png
7
img and mask shape match
ROI centroid= (232, 539)
done!
done!
sampled an abn patch at (x,y) center= (216, 533)
done!
sampled an abn patch at (x,y) center= (231, 574)
done!
sampled an abn patch at (x,y) center= (207, 542)
done!
sampled an abn patch at (x,y) center= (216, 574)
done!
sampled an 

/home/sposso22/Desktop/Breast_cancer/roi/mask_13.png
13
img and mask shape match
ROI centroid= (986, 461)
done!
done!
sampled an abn patch at (x,y) center= (971, 451)
done!
sampled an abn patch at (x,y) center= (986, 492)
done!
sampled an abn patch at (x,y) center= (962, 460)
done!
sampled an abn patch at (x,y) center= (971, 492)
done!
sampled an abn patch at (x,y) center= (946, 447)
done!
sampled an abn patch at (x,y) center= (971, 481)
done!
sampled an abn patch at (x,y) center= (958, 463)
done!
sampled an abn patch at (x,y) center= (999, 482)
done!
sampled an abn patch at (x,y) center= (976, 430)
done!
sampled an abn patch at (x,y) center= (1000, 454)
done!
sampled a bkg patch at (x,y) center= (899, 1164)
done!
sampled a bkg patch at (x,y) center= (798, 142)
done!
sampled a bkg patch at (x,y) center= (363, 1010)
done!
sampled a bkg patch at (x,y) center= (650, 641)
done!
sampled a bkg patch at (x,y) center= (545, 878)
done!
sampled a bkg patch at (x,y) center= (900, 1227)
done!
samp

done!
sampled a bkg patch at (x,y) center= (893, 142)
done!
sampled a bkg patch at (x,y) center= (363, 1010)
done!
sampled a bkg patch at (x,y) center= (650, 641)
done!
sampled a bkg patch at (x,y) center= (545, 878)
done!
sampled a bkg patch at (x,y) center= (900, 1227)
done!
sampled a bkg patch at (x,y) center= (890, 495)
done!
sampled a bkg patch at (x,y) center= (144, 851)
done!
sampled a bkg patch at (x,y) center= (295, 414)
done!
sampled a bkg patch at (x,y) center= (731, 260)
done!
sampled a bkg patch at (x,y) center= (939, 1189)
done!
sampled a bkg patch at (x,y) center= (839, 896)
/home/sposso22/Desktop/Breast_cancer/roi/mask_20.png
20
img and mask shape match
ROI centroid= (329, 707)
done!
done!
sampled an abn patch at (x,y) center= (305, 718)
done!
sampled an abn patch at (x,y) center= (320, 695)
done!
sampled an abn patch at (x,y) center= (296, 727)
done!
sampled an abn patch at (x,y) center= (305, 711)
done!
sampled an abn patch at (x,y) center= (351, 706)
done!
sampled an

26
img and mask shape match
ROI centroid= (487, 653)
done!
done!
sampled an abn patch at (x,y) center= (435, 621)
done!
sampled an abn patch at (x,y) center= (450, 662)
done!
sampled an abn patch at (x,y) center= (554, 630)
done!
sampled an abn patch at (x,y) center= (510, 662)
done!
sampled an abn patch at (x,y) center= (492, 675)
done!
sampled an abn patch at (x,y) center= (538, 617)
done!
sampled an abn patch at (x,y) center= (435, 706)
done!
sampled an abn patch at (x,y) center= (422, 633)
done!
sampled an abn patch at (x,y) center= (471, 621)
done!
sampled an abn patch at (x,y) center= (547, 691)
done!
sampled a bkg patch at (x,y) center= (1015, 1207)
done!
sampled a bkg patch at (x,y) center= (162, 1164)
done!
sampled a bkg patch at (x,y) center= (798, 142)
done!
sampled a bkg patch at (x,y) center= (363, 1010)
done!
sampled a bkg patch at (x,y) center= (650, 641)
done!
sampled a bkg patch at (x,y) center= (545, 878)
done!
sampled a bkg patch at (x,y) center= (900, 1227)
done!
sa

...

ROI centroid= (774, 786)
done!
done!
sampled an abn patch at (x,y) center= (741, 761)
done!
sampled an abn patch at (x,y) center= (756, 802)
done!
sampled an abn patch at (x,y) center= (732, 770)
done!
sampled an abn patch at (x,y) center= (741, 818)
done!
sampled an abn patch at (x,y) center= (816, 802)
done!
sampled an abn patch at (x,y) center= (798, 815)
done!
sampled an abn patch at (x,y) center= (716, 757)
done!
sampled an abn patch at (x,y) center= (741, 791)
done!
sampled an abn patch at (x,y) center= (728, 773)
done!
sampled an abn patch at (x,y) center= (769, 792)
done!
sampled a bkg patch at (x,y) center= (543, 1015)
done!
sampled a bkg patch at (x,y) center= (183, 1186)
done!
sampled a bkg patch at (x,y) center= (899, 1164)
done!
sampled a bkg patch at (x,y) center= (798, 142)
done!
sampled a bkg patch at (x,y) center= (363, 1010)
done!
sampled a bkg patch at (x,y) center= (650, 641)
done!
sampled a bkg patch at (x,y) center= (545, 878)
done!
sampled a bkg patch at (x,y) ce

done!
sampled a bkg patch at (x,y) center= (183, 1186)
done!
sampled a bkg patch at (x,y) center= (899, 1164)
done!
sampled a bkg patch at (x,y) center= (798, 142)
done!
sampled a bkg patch at (x,y) center= (363, 1010)
done!
sampled a bkg patch at (x,y) center= (650, 641)
done!
sampled a bkg patch at (x,y) center= (545, 878)
done!
sampled a bkg patch at (x,y) center= (900, 1227)
done!
sampled a bkg patch at (x,y) center= (890, 495)
done!
sampled a bkg patch at (x,y) center= (144, 851)
done!
sampled a bkg patch at (x,y) center= (731, 260)
/home/sposso22/Desktop/Breast_cancer/roi/mask_3545.png
3545
img and mask shape match
ROI centroid= (327, 652)
done!
done!
sampled an abn patch at (x,y) center= (266, 619)
done!
sampled an abn patch at (x,y) center= (380, 679)
done!
sampled an abn patch at (x,y) center= (307, 661)
done!
sampled an abn patch at (x,y) center= (364, 605)
done!
sampled an abn patch at (x,y) center= (278, 640)
done!
sampled an abn patch at (x,y) center= (354, 633)
done!
samp

ROI centroid= (720, 504)
done!
done!
sampled an abn patch at (x,y) center= (692, 513)
done!
sampled an abn patch at (x,y) center= (707, 490)
done!
sampled an abn patch at (x,y) center= (683, 522)
done!
sampled an abn patch at (x,y) center= (692, 506)
done!
sampled an abn patch at (x,y) center= (767, 490)
done!
sampled an abn patch at (x,y) center= (749, 503)
done!
sampled an abn patch at (x,y) center= (667, 509)
done!
sampled an abn patch at (x,y) center= (692, 495)
done!
sampled an abn patch at (x,y) center= (709, 513)
done!
sampled an abn patch at (x,y) center= (676, 519)
done!
sampled a bkg patch at (x,y) center= (183, 1186)
done!
sampled a bkg patch at (x,y) center= (562, 1164)
done!
sampled a bkg patch at (x,y) center= (798, 142)
done!
sampled a bkg patch at (x,y) center= (363, 1010)
done!
sampled a bkg patch at (x,y) center= (650, 641)
done!
sampled a bkg patch at (x,y) center= (545, 878)
done!
sampled a bkg patch at (x,y) center= (203, 495)
done!
sampled a bkg patch at (x,y) cen

done!
sampled a bkg patch at (x,y) center= (543, 1015)
done!
sampled a bkg patch at (x,y) center= (183, 1186)
done!
sampled a bkg patch at (x,y) center= (899, 1164)
done!
sampled a bkg patch at (x,y) center= (798, 142)
done!
sampled a bkg patch at (x,y) center= (363, 1010)
done!
sampled a bkg patch at (x,y) center= (650, 641)
done!
sampled a bkg patch at (x,y) center= (900, 1227)
done!
sampled a bkg patch at (x,y) center= (890, 495)
done!
sampled a bkg patch at (x,y) center= (144, 851)
done!
sampled a bkg patch at (x,y) center= (295, 414)
/home/sposso22/Desktop/Breast_cancer/roi/mask_3558.png
3558
img and mask shape match
ROI centroid= (651, 640)
done!
done!
sampled an abn patch at (x,y) center= (638, 668)
done!
sampled an abn patch at (x,y) center= (643, 649)
done!
sampled an abn patch at (x,y) center= (684, 625)
done!
sampled an abn patch at (x,y) center= (652, 634)
done!
sampled an abn patch at (x,y) center= (684, 667)
done!
sampled an abn patch at (x,y) center= (613, 635)
done!
sam

img and mask shape match
ROI centroid= (682, 755)
done!
done!
sampled an abn patch at (x,y) center= (663, 761)
done!
sampled an abn patch at (x,y) center= (678, 738)
done!
sampled an abn patch at (x,y) center= (654, 770)
done!
sampled an abn patch at (x,y) center= (663, 754)
done!
sampled an abn patch at (x,y) center= (709, 749)
done!
sampled an abn patch at (x,y) center= (722, 731)
done!
sampled an abn patch at (x,y) center= (664, 756)
done!
sampled an abn patch at (x,y) center= (698, 743)
done!
sampled an abn patch at (x,y) center= (680, 784)
done!
sampled an abn patch at (x,y) center= (699, 761)
done!
sampled a bkg patch at (x,y) center= (522, 1015)
done!
sampled a bkg patch at (x,y) center= (183, 1186)
done!
sampled a bkg patch at (x,y) center= (899, 1164)
done!
sampled a bkg patch at (x,y) center= (798, 142)
done!
sampled a bkg patch at (x,y) center= (363, 1010)
done!
sampled a bkg patch at (x,y) center= (545, 878)
done!
sampled a bkg patch at (x,y) center= (900, 1227)
done!
sampl

In [11]:
s['patch_path'] = s_path
s['label'] = s_class
s.to_csv('/home/sposso22/Desktop/Breast_cancer/patches_256/s.csv',index = False)

In [12]:
s10['patch_path'] = s10_path
s10['label'] = s10_class
s10.to_csv('/home/sposso22/Desktop/Breast_cancer/patches_256/s10.csv',index = False)

In [13]:
len(s10)

71360

In [14]:
3568*2*10

71360